In [2]:
from google.colab import drive 
drive.mount('/content/gdrive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/gdrive


In [3]:
%cd /content/gdrive/My\ Drive/spngp

/content/gdrive/My Drive/spngp


In [5]:
!pip install gpytorch

     |████████████████████████████████| 245kB 7.5MB/s 
  Created wheel for gpytorch: filename=gpytorch-1.1.1-py2.py3-none-any.whl size=400467 sha256=1696a6af7e743b745b34cadc3efffb77e84e64c4b9c2a29a85ca747ac78e843c
  Stored in directory: /root/.cache/pip/wheels/e5/a5/29/4dafc0624adf678108e0067836556f0c72588e85d851d78ae0
Successfully built gpytorch


In [0]:
import tqdm
import math
import torch
import gpytorch
import numpy as np
from matplotlib import pyplot as plt
import urllib.request
import os
import time
from scipy.io import loadmat
import pandas as pd
import sys
from math import floor

# Make plots inline
%matplotlib inline

In [0]:
data = pd.read_csv('spngp/datasets/ccpp/ccpp.csv')
data = pd.DataFrame(data).dropna() # miss = data.isnull().sum()/len(data)
dmean, dstd = data.mean(), data.std()
data = (data-dmean)/dstd

train = data.sample(frac=0.8, random_state=58)
test  = data.drop(train.index)
x, y = train.iloc[:, :-1].values, train.iloc[:, -1].values.reshape(-1,1)
x_test, y_test = test.iloc[:, :-1].values, test.iloc[:, -1].values.reshape(-1,1)

In [0]:
x = np.array(x,dtype='float32')
y = np.array(y,dtype='float32')
x_test = np.array(x_test,dtype='float32')
y_test = np.array(y_test,dtype = 'float32')

In [0]:
train_x = torch.tensor(x).contiguous()
train_y = torch.tensor(y).contiguous()
#torch.reshape(train_y,(-1,))
test_x = torch.tensor(x_test).contiguous()
test_y = torch.tensor(y_test).contiguous()
#torch.reshape(test_y,(-1,))

if torch.cuda.is_available():
    train_x, train_y, test_x, test_y = train_x.cuda(), train_y.cuda(), test_x.cuda(), test_y.cuda()

In [0]:
from torch.utils.data import TensorDataset, DataLoader
train_dataset = TensorDataset(train_x, train_y)
train_loader = DataLoader(train_dataset, batch_size= 1024, shuffle=True)

test_dataset = TensorDataset(test_x, test_y)
test_loader = DataLoader(test_dataset, batch_size=1024, shuffle=False)

In [0]:
from gpytorch.models import ApproximateGP
from gpytorch.variational import CholeskyVariationalDistribution
from gpytorch.variational import VariationalStrategy

class GPModel(ApproximateGP):
    def __init__(self, inducing_points):
        variational_distribution = CholeskyVariationalDistribution(inducing_points.size(0))
        variational_strategy = VariationalStrategy(self, inducing_points, variational_distribution, learn_inducing_locations=True)
        super(GPModel, self).__init__(variational_strategy)
        self.mean_module = gpytorch.means.ConstantMean()
        self.covar_module = gpytorch.kernels.ScaleKernel(gpytorch.kernels.RBFKernel())

    def forward(self, x):
        mean_x = self.mean_module(x)
        covar_x = self.covar_module(x)
        return gpytorch.distributions.MultivariateNormal(mean_x, covar_x)

inducing_points = train_x[:500, :]
model = GPModel(inducing_points=inducing_points)
likelihood = gpytorch.likelihoods.GaussianLikelihood()

if torch.cuda.is_available():
    model = model.cuda()
    likelihood = likelihood.cuda()

In [72]:
num_epochs = 500

model.train()
likelihood.train()

# We use SGD here, rather than Adam. Emperically, we find that SGD is better for variational regression
optimizer = torch.optim.Adam([
    {'params': model.parameters()},
    {'params': likelihood.parameters()},
], lr=0.01)

# Our loss object. We're using the VariationalELBO
mll = gpytorch.mlls.VariationalELBO(likelihood, model, num_data=train_y.size(0))
epochs_iter = tqdm.notebook.tqdm(range(num_epochs), desc="Epoch")
start_time = time.time()
for i in epochs_iter:
    # Within each iteration, we will go over each minibatch of data
    minibatch_iter = tqdm.notebook.tqdm(train_loader, desc="Minibatch", leave=False)
    for x_batch, y_batch in minibatch_iter:
        optimizer.zero_grad()
        output = model(x_batch)
        loss = -mll(output, y_batch)
        loss = loss.sum()
        minibatch_iter.set_postfix(loss=loss.item())
        loss.backward()
        optimizer.step()
        print('Epoch: ',i,' Loss: ', loss)

model.eval()
likelihood.eval()
means = torch.tensor([0.])
with torch.no_grad():
      preds = model(test_x)
      means = torch.cat([means, preds.mean.cpu()])
means = means[1:]

end_time = time.time()
time_var = end_time - start_time

Epoch:  0  Loss:  tensor(1432.7080, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  0  Loss:  tensor(1472.7415, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  0  Loss:  tensor(1460.2078, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  0  Loss:  tensor(1456.7157, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  0  Loss:  tensor(1488.3203, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  0  Loss:  tensor(1464.0284, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  0  Loss:  tensor(1456.2886, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  0  Loss:  tensor(579.5651, device='cuda:0', grad_fn=<SumBackward0>)


Epoch:  1  Loss:  tensor(1491.3630, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  1  Loss:  tensor(1465.3845, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  1  Loss:  tensor(1463.7675, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  1  Loss:  tensor(1458.1260, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  1  Loss:  tensor(1456.4172, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  1  Loss:  tensor(1444.3838, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  1  Loss:  tensor(1440.2604, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  1  Loss:  tensor(585.4774, device='cuda:0', grad_fn=<SumBackward0>)


Epoch:  2  Loss:  tensor(1473.6750, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  2  Loss:  tensor(1478.1924, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  2  Loss:  tensor(1430.6985, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  2  Loss:  tensor(1447.9785, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  2  Loss:  tensor(1460.3215, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  2  Loss:  tensor(1451.7458, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  2  Loss:  tensor(1462.2810, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  2  Loss:  tensor(594.7649, device='cuda:0', grad_fn=<SumBackward0>)


Epoch:  3  Loss:  tensor(1466.1327, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  3  Loss:  tensor(1465.3367, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  3  Loss:  tensor(1428.6796, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  3  Loss:  tensor(1487.6274, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  3  Loss:  tensor(1456.0918, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  3  Loss:  tensor(1444.0740, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  3  Loss:  tensor(1450.1650, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  3  Loss:  tensor(598.0569, device='cuda:0', grad_fn=<SumBackward0>)


Epoch:  4  Loss:  tensor(1461.8777, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  4  Loss:  tensor(1453.2388, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  4  Loss:  tensor(1447.2181, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  4  Loss:  tensor(1449.7837, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  4  Loss:  tensor(1463.9202, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  4  Loss:  tensor(1448.8993, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  4  Loss:  tensor(1472.3896, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  4  Loss:  tensor(597.9397, device='cuda:0', grad_fn=<SumBackward0>)


...

Epoch:  495  Loss:  tensor(1480.9874, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  495  Loss:  tensor(1435.0818, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  495  Loss:  tensor(1472.2180, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  495  Loss:  tensor(1454.3677, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  495  Loss:  tensor(1438.2236, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  495  Loss:  tensor(1451.4574, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  495  Loss:  tensor(1466.6317, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  495  Loss:  tensor(565.1039, device='cuda:0', grad_fn=<SumBackward0>)


Epoch:  496  Loss:  tensor(1466.2695, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  496  Loss:  tensor(1477.5068, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  496  Loss:  tensor(1430.4944, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  496  Loss:  tensor(1457.9053, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  496  Loss:  tensor(1458.6569, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  496  Loss:  tensor(1452.7671, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  496  Loss:  tensor(1440.8149, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  496  Loss:  tensor(579.6960, device='cuda:0', grad_fn=<SumBackward0>)


Epoch:  497  Loss:  tensor(1450.9843, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  497  Loss:  tensor(1478.4822, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  497  Loss:  tensor(1443.5548, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  497  Loss:  tensor(1435.7692, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  497  Loss:  tensor(1466.6287, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  497  Loss:  tensor(1459.8298, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  497  Loss:  tensor(1461.1997, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  497  Loss:  tensor(566.8611, device='cuda:0', grad_fn=<SumBackward0>)


Epoch:  498  Loss:  tensor(1449.4397, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  498  Loss:  tensor(1453.3082, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  498  Loss:  tensor(1440.4741, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  498  Loss:  tensor(1457.0137, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  498  Loss:  tensor(1437.9712, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  498  Loss:  tensor(1459.5696, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  498  Loss:  tensor(1463.4840, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  498  Loss:  tensor(602.1791, device='cuda:0', grad_fn=<SumBackward0>)


Epoch:  499  Loss:  tensor(1442.1450, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  499  Loss:  tensor(1450.9902, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  499  Loss:  tensor(1465.1958, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  499  Loss:  tensor(1455.3473, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  499  Loss:  tensor(1494.2064, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  499  Loss:  tensor(1424.9761, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  499  Loss:  tensor(1445.4114, device='cuda:0', grad_fn=<SumBackward0>)
Epoch:  499  Loss:  tensor(585.1182, device='cuda:0', grad_fn=<SumBackward0>)



In [73]:
print(time_var)

177.55233788490295


In [74]:
print('Test MAE: {}'.format(torch.mean(torch.abs(means - test_y.cpu()))))


Test MAE: 0.8624453544616699


In [75]:
mn = (mean.ravel() * dstd.iloc[-1]) + dmean.iloc[-1]
mu_t = (test.iloc[:, -1]*dstd.iloc[-1]) + dmean.iloc[-1]
sqe = (mn - mu_t.values)**2
rmse_var = np.sqrt(sqe.sum()/len(test))
print(rmse_var)

16.961268862942322
